# Class 16

## library

In [5]:
import sqlite3
import random
import hashlib
import time
from datetime import date
from itertools import permutations

## Exercise 1: Password hashing and salting

In [6]:
def connect ():
  try:
    conn = sqlite3.connect('users.db', timeout=100)  # Set a timeout to avoid locking
    c = conn.cursor()
    c.execute('''CREATE TABLE IF NOT EXISTS users
               (username TEXT UNIQUE, password TEXT, salt TEXT)''')
    conn.commit()
    return conn
  except sqlite3.OperationalError as e:
    print(f"Database error: {e}")
    return None

def hash_password_with_salt (password, salt=random.randint(0, 100)):
  salt = str(salt)
  password += str(salt)
  password = password.encode()
  hashed_password = hashlib.sha256(password).hexdigest()
  return hashed_password, salt

def register (username, password):
  conn = connect()
  password_hash, salt = hash_password_with_salt(password)
  c = conn.cursor()
  try:
    c.execute("INSERT INTO users VALUES (?,?,?)", (username, password_hash, salt))
    conn.commit()
    print(f"{username} is registered completely")
  except sqlite3.IntegrityError as e:
    print(f"Database error: {e}")
  finally:
    close_connect(conn)

def login (username, password):
  conn = connect()
  c = conn.cursor()
  c.execute("SELECT * FROM users WHERE username=?", (username,))
  user = c.fetchone()
  close_connect(conn)
  if user:
    salt = user[2]
    hashed_password, _ = hash_password_with_salt(password, salt)
    if hashed_password == user[1]:
      return True
  return False

def close_connect(conn):
  if conn:
    conn.close()

In [7]:
# test registration
register('user1', 'password1')
print(login('user1', 'password1')) # True
print(login('user1', 'wrong_password')) # False

user1 is registered completely
True
False


## Exercise 2: General dictionary attacks

In [4]:
target = "3ddcd95d2bff8e97d3ad817f718ae207b98c7f2c84c5519f89cd15d7f8ee1c3b"

def read_dict_txt():
  with open('phpbb.txt', 'r') as f:
    return [line.strip() for line in f]

def hash_password(password):
  password = password.encode()
  hashed_password = hashlib.sha256(password).hexdigest()
  return hashed_password

dictionary = read_dict_txt()
for word in dictionary:
  h = hash_password(word)
  if h == target:
    print(f"Found password: {word}")
    break
  else:
    print(f"{word}: {h}")

123456: 8d969eef6ecad3c29a3a629280e686cf0c3f5d5a86aff3ca12020c923adc6c92
password: 5e884898da28047151d0e56f8dc6292773603d0d6aabbdd62a11ef721d1542d8
phpbb: 00451d9a00bf9b7b39579402195ea63bad0a1d73c8259608057ea7bcd9d37f07
qwerty: 65e84be33532fb784c48129675f9eff3a682b27168c0ea744b2cf58ee02337c5
12345: 5994471abb01112afcc18159f6cc74b4f511b99806da59b3caf5a9c173cacfc5
12345678: ef797c8118f02dfb649607dd5d3f8c7623048c9c063d532cc95c5ed7a898a64f
letmein: 1c8bfe8f801d79745c4631d09fff36c82aa37fc4cce4fc946683d7b336b63032
111111: bcb15f821479b4d5772bd0ca866c00ad5f926e3580720659cc80d39c9d09802a
1234: 03ac674216f3e15c761ee1a5e255f067953623c8b388b4459e13f978d7c846f4
123456789: 15e2b0d3c33891ebb0f1ef609ec419420c20e320ce94c65fbc8c3312448eb225
abc123: 6ca13d52ca70c883e0f0bb101e425a89e8624de51db2d2392593af6a84118090
test: 9f86d081884c7d659a2feaa0c55ad015a3bf4f1b2b0b822cd15d6c15b0f00a08
123123: 96cae35ce8a9b0244178bf28e4966c2ce1b8385723a96a6b838858cdd6ca0a1e
123: a665a45920422f9d417e4867efdc4fb8a04a1f3fff1f

## Exercise 4: Breaking a graphical password (an Android unlock pattern)

In [5]:
# Given hash value
target = "91077079768edba10ac0c93b7108bc639d778d67"

# Define the points on the grid
points = ['a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i']

# Function to hash the pattern using SHA-1
def hash_pattern(pattern):
    pattern_str = ''.join(pattern)
    return hashlib.sha1(pattern_str.encode()).hexdigest()

# Brute-force all possible unlock patterns
def find_unlock_pattern(target):
    # Lengths of patterns can vary from 4 to 9
    for length in range(4, 10):
        for pattern in permutations(points, length):
            hashed_pattern = hash_pattern(pattern)
            if hashed_pattern == target:
                print(f"Unlock pattern found: {pattern}")
                return pattern
    print("Unlock pattern not found.")
    return None

# Run the function to find the unlock pattern
find_unlock_pattern(target)


Unlock pattern found: ('a', 'e', 'b', 'f', 'c', 'i', 'd', 'h', 'g')


('a', 'e', 'b', 'f', 'c', 'i', 'd', 'h', 'g')

## Exercise 3: Personalised dictionary attack

In [8]:
salt = "5UA@/Mw^%He]SBaU"

# Personal information dictionary
info = {
    "username": "laplusbelle",
    "name": "Marie",
    "surname": "Curie",
    "pet": "Woof",
    "birthdate": date(1980, 1, 2),
    "employer": "UKC",
    "mother_first_name": "Jean",
    "mother_last_name": "Neoskour",
    "father_first_name": "Jvaist",
    "father_last_name": "Fairecourir",
    "husband": "Eltrofor",
    "husband_birthdate": date(1981, 12, 29)
}

# Function to format a date in multiple formats
def format_date(date):
    return list(set([str(int(date.strftime(fmt))) for fmt in [
        "%d", "%m"
    ]] + [date.strftime(fmt) for fmt in [
        "%d", "%m", "%y", "%Y"
    ]] + [date.strftime(fmt) for fmt in [
        "%b", "%B"
    ]]))

# Function to gather all information pieces into a list
def info_list():
    result_list = [info[key] for key in info.keys() if type(info[key]) is str]
    for key in info:
        if type(info[key]) is not str:
            result_list += format_date(info[key])
    return result_list

def format_styles(combo):
    camel_case = combo[0].lower() + ''.join(word.capitalize() for word in combo[1:])
    pascal_case = ''.join(word.capitalize() for word in combo)
    snake_case = '_'.join(word.lower() for word in combo)
    kebab_case = '-'.join(word.lower() for word in combo)
    all_uppercase = '_'.join(word.upper() for word in combo)

    return set([
      camel_case,
      pascal_case,
      snake_case,
      kebab_case,
      all_uppercase
    ])

# Split dates into various formats
birthday_formats = format_date(info["birthdate"])
husband_birthday_formats = format_date(info["husband_birthdate"])

# Create basic dictionary words list
base_words = [v for v in info.values() if type(v) is str] + husband_birthday_formats + birthday_formats

dictionary = []

def generate_dictionary(length, target):
    print(f"Target: {target}")
    with open("wordlist.txt", "a") as word:
      for combo in permutations(base_words, length):
        for pwd in format_styles(combo):
        # pwd = ''.join(word.capitalize() for word in combo)  # Example style: PascalCase
          if pwd not in dictionary:
              dictionary.append(pwd)
              h = hash_password(pwd+salt)
              word.write(f"{pwd}\n")
              if h == target:
                return pwd
    print(f"{len(dictionary)} passwords")
    return None

print(f"total base words: {len(base_words)} words")

total base words: 24 words


In [ ]:
target = "3281e6de7fa3c6fd6d6c8098347aeb06bd35b0f74b96f173c7b2d28135e14d45" # -> Woof122981Eltrofor

for length in range(1, len(base_words)):
  start_time = time.time()
  print(f"Length: {length}")
  res = generate_dictionary(length, target)

  end_time = time.time()  # Record end time
  elapsed_time = end_time - start_time
  print(f"Elapsed Time: {elapsed_time} seconds")
  if res:
    print(f"Password found: {res}")
    break
  else:
    print(f"No password found for length {length}.")

Length: 1
Target: 3281e6de7fa3c6fd6d6c8098347aeb06bd35b0f74b96f173c7b2d28135e14d45
24 passwords
No password found for length 1.
Elapsed Time: 0.0015492439270019531 seconds
Length: 2
Target: 3281e6de7fa3c6fd6d6c8098347aeb06bd35b0f74b96f173c7b2d28135e14d45
575 passwords
No password found for length 2.
Elapsed Time: 0.009926795959472656 seconds
Length: 3
Target: 3281e6de7fa3c6fd6d6c8098347aeb06bd35b0f74b96f173c7b2d28135e14d45
12676 passwords
No password found for length 3.
Elapsed Time: 2.0670671463012695 seconds
Length: 4
Target: 3281e6de7fa3c6fd6d6c8098347aeb06bd35b0f74b96f173c7b2d28135e14d45
266377 passwords
No password found for length 4.
Elapsed Time: 702.2041480541229 seconds
Length: 5
Target: 3281e6de7fa3c6fd6d6c8098347aeb06bd35b0f74b96f173c7b2d28135e14d45
Password found: Woof122981Eltrofor


In [11]:
target = "fc2298f491eac4cff95e7568806e088a901c904cda7dd3221f551e5b89b3c3aa" # ->

for length in range(7, len(base_words)):
  start_time = time.time()
  print(f"Length: {length}")
  res = generate_dictionary(length, target)

  end_time = time.time()  # Record end time
  elapsed_time = end_time - start_time
  if res:
    print(f"Password found: {res}")
    break
  else:
    print(f"No password found for length {length}.")
  print(f"Elapsed Time: {elapsed_time} seconds")

Length: 7
Target: fc2298f491eac4cff95e7568806e088a901c904cda7dd3221f551e5b89b3c3aa


KeyboardInterrupt: 